<table width="100%" style="padding:0; margin-left:-6px;">
    <tr style="padding=0;" width="100%">
        <td width="auto">
           <hr style="border:2px solid darkblue">
            <h1> nb8. Query using astroquery</h1>
           <hr style="border:2px solid darkblue">
        </td>
        <td width="60px">
           <img src="ALMAsmall.png" align="right"/> 
        </td>
    </tr>
</table>  

In a similar manner to the previous notebooks, it is also possible to run TAP queries using the [astroquery](https://astroquery.readthedocs.io/en/latest/alma/alma.html) Python package. 

The very lastest version of astroquery is needed. This can be installed with:
```bash
pip3 install --upgrade --pre astroquery
```

In [1]:
from astroquery.alma import Alma
import numpy as np
import astropy

You can obtain keywords, description and units of the ALMA TAP service by calling:

In [2]:
Alma.help()


Most common ALMA query keywords are listed below. These keywords are part of the ALMA ObsCore model, an IVOA standard for metadata representation (3rd column). They were also present in original ALMA Web form and, for backwards compatibility can be accessed with their old names (2nd column).
More elaborate queries on the ObsCore model are possible with `query_sia` or `query_tap` methods
  Description                       Original ALMA keyword               ObsCore keyword                    
-------------------------------------------------------------------------------------------------------

Position
  Source name (astropy Resolver)    source_name_resolver                SkyCoord.from_name                 
  Source name (ALMA)                source_name_alma                    target_name                        
  RA Dec (Sexagesimal)              ra_dec                              s_ra, s_dec                        
  Galactic (Degrees)                galactic                   

-----------------------------------------

## Example 8a: Query one object by a resolved source name and then by coordinates using TAP

This is equivalent to the queries we show in notebook 1.

In [3]:
coordinates = astropy.coordinates.SkyCoord.from_name("Cen A")
output = Alma.query_tap(f"SELECT * FROM ivoa.obscore WHERE INTERSECTS(CIRCLE('ICRS',{coordinates.ra.degree},{coordinates.dec.degree},0.16),s_region)=1").to_table().to_pandas()
output.head(5)

access_url access_format  \
0  http://almascience.org/aq?member_ous_id=uid://...     text/html   
1  http://almascience.org/aq?member_ous_id=uid://...     text/html   
2  http://almascience.org/aq?member_ous_id=uid://...     text/html   
3  http://almascience.org/aq?member_ous_id=uid://...     text/html   
4  http://almascience.org/aq?member_ous_id=uid://...     text/html   

       proposal_id data_rights  gal_longitude  gal_latitude  \
0  2011.0.00008.SV      Public     309.512363     19.416239   
1  2011.0.00008.SV      Public     309.512363     19.416239   
2  2011.0.00008.SV      Public     309.512363     19.416239   
3  2011.0.00008.SV      Public     309.512363     19.416239   
4   2011.0.00010.S      Public     309.515914     19.417224   

              obs_publisher_did obs_collection facility_name instrument_name  \
0  ADS/JAO.ALMA#2011.0.00008.SV           ALMA           JAO            ALMA   
1  ADS/JAO.ALMA#2011.0.00008.SV           ALMA           JAO            ALMA   
2  ADS/JAO.ALMA#2011.0.00008.SV           ALMA           JAO            ALMA   
3  ADS/JAO.ALMA#2011.0.00008.SV           ALMA           JAO            ALMA   
4   ADS/JAO.ALMA#2011.0.00010.S           ALMA           JAO            ALMA   

   ...   frequency velocity_resolution   obs_creator_name  \
0  ...  238.261613         1183.847494  observatory, ALMA   
1  ...  238.261613         1183.847494  observatory, ALMA   
2  ...  238.261613         1183.847494  observatory, ALMA   
3  ...  238.261613         1183.847494  observatory, ALMA   
4  ...  219.025328          663.940713       Ott, Juergen   

                                           pub_title  \
0  ALMA Observations of the Physical and Chemical...   
1  ALMA Observations of the Physical and Chemical...   
2  ALMA Observations of the Physical and Chemical...   
3  ALMA Observations of the Physical and Chemical...   
4  ALMA Observations of the Physical and Chemical...   

                                 first_author  qa2_passed  \
0  Azeez, Jazeel H. Israel, F. P. McCoy, Mark           T   
1  Azeez, Jazeel H. Israel, F. P. McCoy, Mark           T   
2  Azeez, Jazeel H. Israel, F. P. McCoy, Mark           T   
3  Azeez, Jazeel H. Israel, F. P. McCoy, Mark           T   
4                                 McCoy, Mark           T   

                                       bib_reference  \
0  2014A&A...562A..96I 2017AdAst2017E...6A 2017Ap...   
1  2014A&A...562A..96I 2017AdAst2017E...6A 2017Ap...   
2  2014A&A...562A..96I 2017AdAst2017E...6A 2017Ap...   
3  2014A&A...562A..96I 2017AdAst2017E...6A 2017Ap...   
4                                2017ApJ...851...76M   

                                     science_keyword  scientific_category  \
0  Galactic centres/nuclei, Active Galactic Nucle...      Active galaxies   
1  Galactic centres/nuclei, Active Galactic Nucle...      Active galaxies   
2  Galactic centres/nuclei, Active Galactic Nucle...      Active galaxies   
3  Galactic centres/nuclei, Active Galactic Nucle...      Active galaxies   
4  Active Galactic Nuclei (AGN)/Quasars (QSO), Me...      Active galaxies   

              lastModified  
0  2021-09-30T16:34:41.133  
1  2021-09-30T16:34:41.133  
2  2021-09-30T16:34:41.133  
3  2021-09-30T16:34:41.133  
4  2021-09-30T16:34:41.133  

[5 rows x 63 columns]

Print all the target names associated with these coordinates:

In [4]:
np.unique(output['target_name']) 

array(['1322-427', '3FGL_J1325.4-4301', 'CenA', 'Cen_A', 'Centaurus A',
       'Centaurus_A', 'Centaurus_a', 'J1325-430', 'J1325-4301',
       'NGC_5128'], dtype=object)

-------------------------------------------

## Example 8b: Query one object by the ALMA source name, using the standard astroquery

As in notebook 1, querying by source name should use the name resolver, e.g. Example 8a. Only in very special occasions it can be useful to query for the source name that the PI has put into their proposal. Many sources have a large variety of different names.

In [5]:
output = Alma.query({'source_name_alma': 'CenA'}).to_pandas()
output.head(5)

access_url access_format  \
0  http://almascience.org/aq?member_ous_id=uid://...     text/html   
1  http://almascience.org/aq?member_ous_id=uid://...     text/html   
2  http://almascience.org/aq?member_ous_id=uid://...     text/html   
3  http://almascience.org/aq?member_ous_id=uid://...     text/html   
4  http://almascience.org/aq?member_ous_id=uid://...     text/html   

      proposal_id data_rights  gal_longitude  gal_latitude  \
0  2011.0.00010.S      Public     309.515914     19.417224   
1  2011.0.00010.S      Public     309.515914     19.417224   
2  2011.0.00010.S      Public     309.515914     19.417224   
3  2011.0.00010.S      Public     309.515914     19.417224   
4  2011.0.00010.S      Public     309.515914     19.417224   

             obs_publisher_did obs_collection facility_name instrument_name  \
0  ADS/JAO.ALMA#2011.0.00010.S           ALMA           JAO            ALMA   
1  ADS/JAO.ALMA#2011.0.00010.S           ALMA           JAO            ALMA   
2  ADS/JAO.ALMA#2011.0.00010.S           ALMA           JAO            ALMA   
3  ADS/JAO.ALMA#2011.0.00010.S           ALMA           JAO            ALMA   
4  ADS/JAO.ALMA#2011.0.00010.S           ALMA           JAO            ALMA   

   ...   frequency velocity_resolution  obs_creator_name  \
0  ...  111.417365          322.835911      Ott, Juergen   
1  ...  111.417365          322.835911      Ott, Juergen   
2  ...  111.417365          322.835911      Ott, Juergen   
3  ...  111.417365          322.835911      Ott, Juergen   
4  ...   92.655678          368.331902      Ott, Juergen   

                                           pub_title  first_author  \
0  ALMA Observations of the Physical and Chemical...   McCoy, Mark   
1  ALMA Observations of the Physical and Chemical...   McCoy, Mark   
2  ALMA Observations of the Physical and Chemical...   McCoy, Mark   
3  ALMA Observations of the Physical and Chemical...   McCoy, Mark   
4  ALMA Observations of the Physical and Chemical...   McCoy, Mark   

   qa2_passed        bib_reference  \
0           T  2017ApJ...851...76M   
1           T  2017ApJ...851...76M   
2           T  2017ApJ...851...76M   
3           T  2017ApJ...851...76M   
4           T  2017ApJ...851...76M   

                                     science_keyword  scientific_category  \
0  Active Galactic Nuclei (AGN)/Quasars (QSO), Me...      Active galaxies   
1  Active Galactic Nuclei (AGN)/Quasars (QSO), Me...      Active galaxies   
2  Active Galactic Nuclei (AGN)/Quasars (QSO), Me...      Active galaxies   
3  Active Galactic Nuclei (AGN)/Quasars (QSO), Me...      Active galaxies   
4  Active Galactic Nuclei (AGN)/Quasars (QSO), Me...      Active galaxies   

              lastModified  
0  2021-09-30T16:34:41.133  
1  2021-09-30T16:34:41.133  
2  2021-09-30T16:34:41.133  
3  2021-09-30T16:34:41.133  
4  2021-09-30T16:34:41.133  

[5 rows x 63 columns]

-------------------------------------------

## Example 8c: Query one object by resolved ALMA source name, using TAP through astroquery

Similar to notebook 1, TAP can also be used for the queries through Astroquery. In SQL, the % is the special character for "any string", equivalent to * in the shell. Similarly, in SQL the _ is the special character for "any character", equivalent to ? in the shell.

In [6]:
output = Alma.query_tap(f"SELECT * FROM ivoa.obscore WHERE target_name like '%Cen%A%'").to_table().to_pandas()

The variations of the source name which include 'Cen' and 'A' are the following:

In [7]:
np.unique(output['target_name']) 

array(['Cen A - Xray N5', 'CenA', 'CenA - CO knot S1', 'CenA - Xray N1',
       'CenA - Xray N2', 'CenA - Xray N3', 'CenA - Xray N4', 'Cen_A',
       'Centaurus A', 'Centaurus_A'], dtype=object)